In [43]:
import torch
from torch import nn
from torch.autograd import Variable
import random
import numpy as np
from tqdm import tqdm
import string

In [57]:
eng_letters = string.ascii_letters + " .,;!?'"
n_eng_letters = len(eng_letters)
print(eng_letters)

abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ .,;!?'


In [96]:
inFile = open("deu-eng/deu.txt", "r")

In [97]:
Xs = []
Ys = []
length = sum(1 for line in inFile)
print(length)

159204


In [98]:
inFile.seek(0)
for line in inFile:
    for stripped in line.split('\n'):
        dp = stripped.split('\t')
        if len(dp) == 2:
            Xs.append(dp[0])
            Ys.append(dp[1])

In [25]:
max_eng_length = len(max(Xs, key=len))
print(max_eng_length)

286


In [27]:
print(Xs, len(Xs))

['Hi.', 'Hi.', 'Run!', 'Wow!', 'Wow!', 'Fire!', 'Help!', 'Help!', 'Stop!', 'Wait!', 'Hello!', 'I try.', 'I won!', 'I won!', 'Smile.', 'Cheers!', 'Freeze!', 'Freeze!', 'Got it?', 'Got it?', 'He ran.', 'He ran.', 'Hop in.', 'Hug me.', 'Hug me.', 'Hug me.', 'I fell.', 'I fell.', 'I fell.', 'I fell.', 'I fell.', 'I know.', 'I lied.', 'I lost.', "I'm 19.", "I'm 19.", "I'm OK.", "I'm OK.", 'No way!', 'No way!', 'No way!', 'No way!', 'Really?', 'Really?', 'Really?', 'Thanks.', 'Try it.', 'Why me?', 'Ask Tom.', 'Ask Tom.', 'Ask Tom.', 'Be cool.', 'Be fair.', 'Be fair.', 'Be nice.', 'Be nice.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Beat it.', 'Call me.', 'Come in.', 'Come in.', 'Come on!', 'Come on!', 'Come on!', 'Come on!', 'Get out!', 'Go away!', 'Go away!', 'Go away!', 'Go away!', 'Go away!', 'Go away!', 'Go away!', 'Go away!', 'Go away!',

In [ ]:
print(y_train)

# Making LSTM Encoder and Decoder Layers

In [101]:
class LSTM(nn.Module):
    def __init__(self, num_layers, input_size, hidden_size, output_size):
        super(LSTM, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers

        self.input_to_hidden = nn.Linear(input_size + hidden_size, hidden_size)
        self.input_to_output = nn.Linear(input_size + hidden_size, output_size)
        self.activation = nn.LogSoftmax(dim=1)
        
    def forward(self, inp, hidden): 
        print(inp.size(), hidden.size())
        combined = torch.cat((inp,hidden),1)
        output = self.activation(self.input_to_output(combined))
        new_hidden = self.input_to_hidden(combined)
        state_h, state_c = new_hidden
        return output, state_h, state_c
        
    def initHidden(self):
        return Variable(torch.zeros(1, self.hidden_size))

In [102]:
enc_num_layers = 1
enc_input_size = n_eng_letters
enc_hidden_size = 286
enc_output_size = 10 #doesn't matter
print(enc_hidden_size)

286


In [103]:
enc = LSTM(enc_num_layers, enc_input_size, enc_hidden_size, enc_output_size)

In [95]:
def letterToIndex(letter):
    return eng_letters.find(letter)

# turn a letter into a <1 x n_letters> Tensor
def letterToTensor(letter):
    tensor = torch.zeros(1, n_eng_letters)
    tensor[0][letterToIndex(letter)] = 1
    return tensor

# Turn a line into a <max eng length x 1 x n_letters>,
# or an array of one-hot letter vectors
# adds padding
def lineToTensor(line):
    tensor = torch.zeros(max_eng_length, 1, n_eng_letters)
    for li, letter in enumerate(line):
        tensor[li][0][letterToIndex(letter)] = 1
    return tensor

In [99]:
for s in tqdm(range(len(Xs))):
    Xs[s] = Variable(lineToTensor(Xs[s]))
hidden = Variable(torch.zeros(1, enc_hidden_size))

100%|██████████| 159204/159204 [00:24<00:00, 6459.65it/s]


In [104]:
enc_output, state_h, state_c = enc(Xs[0], hidden)

torch.Size([286, 1, 59]) torch.Size([1, 286])


RuntimeError: inconsistent tensor sizes at /Users/soumith/code/builder/wheel/pytorch-src/torch/lib/TH/generic/THTensorMath.c:2864